In [19]:
import sys
sys.path.append('../src')
import pandas as pd
import folium

# Load CSV data
county_data = pd.read_csv("../DATA/dev/new_england_counties2019.csv")
bus_data = pd.read_csv("../DATA/dev/NewEngland-HVbuses.csv")

# Verify columns
if 'Lon' not in bus_data.columns or 'Lat' not in bus_data.columns:
    raise ValueError("Your dataset must contain 'Lat' and 'Lon' columns.")
if 'Lat' not in county_data.columns or 'Lon' not in county_data.columns:
    raise ValueError("The counties dataset must contain 'Lat' and 'Lon' columns.")

# Center longitude of New England
center_longitude = -71.5

# Reflect longitude over the center line
def reflect_longitude(lon, center_lon=center_longitude):
    return 2 * center_lon - lon

# Apply the reflection to the longitude of each data point
county_data['Lon'] = county_data['Lon'].apply(reflect_longitude)
bus_data['Lon'] = bus_data['Lon'].apply(reflect_longitude)

# Step 1: Calculate the average coordinates of the counties
avg_lat_county = county_data['Lat'].mean()
avg_lon_county = county_data['Lon'].mean()

# Step 2: Define the center of New England
new_england_center_lat = 43.0
new_england_center_lon = center_longitude

# Step 3: Calculate the offset based on the average position
lat_offset = new_england_center_lat - avg_lat_county
lon_offset = new_england_center_lon - avg_lon_county

# Step 4: Apply the offsets to the bus_data
bus_data['Lat'] = bus_data['Lat'] + lat_offset
bus_data['Lon'] = bus_data['Lon'] + lon_offset

# Step 5: Apply the offsets to the county_data (if necessary, for consistency)
county_data['Lat'] = county_data['Lat'] + lat_offset
county_data['Lon'] = county_data['Lon'] + lon_offset

# Step 6: Center the map on New England
us_map = folium.Map(location=[new_england_center_lat, new_england_center_lon], zoom_start=7)

# Define bus type colors
bus_type_colors = {
    1: "blue",
    2: "green",
    3: "red",
    4: "gray"
}

# Plot buses
for _, row in bus_data.iterrows():
    lat, lon = row["Lat"], row["Lon"]
    bus_type = row["type"]
    bus_id = row["bus_id"]
    Pd, Qd = row["Pd"], row["Qd"]
    
    tooltip = f"Bus ID: {bus_id}<br>Type: {bus_type}<br>Pd: {Pd} MW<br>Qd: {Qd} MVAr"
    
    folium.CircleMarker(
        location=(lat, lon),
        radius=2,
        color=bus_type_colors.get(bus_type, "black"),
        fill=True,
        fill_color=bus_type_colors.get(bus_type, "black"),
        fill_opacity=0.7,
        tooltip=tooltip
    ).add_to(us_map)

# Plot counties
for _, row in county_data.iterrows():
    lat, lon = row["Lat"], row["Lon"]
    county_name, state = row["County"], row["State"]
    offshore_wind_allowed = row["offshore-wind-allowed"]
    
    triangle_vertices = [
        (lat, lon),
        (lat + 0.1, lon + 0.1),
        (lat - 0.1, lon + 0.1),
    ]
    
    tooltip = f"County: {county_name}, {state}<br>Offshore Wind Allowed: {offshore_wind_allowed}, Lat: {lat}, Lon: {lon}"
    
    folium.Polygon(
        locations=triangle_vertices,
        color="red",
        fill=True,
        fill_color="red",
        fill_opacity=0.5,
        tooltip=tooltip
    ).add_to(us_map)

# Save and visualize the map
# us_map.save("new_england_map.html")
us_map
